In [1]:
import pandas as pd
import tweepy
import re
import numpy as np
import os
import demoji
import emoji
from bs4 import BeautifulSoup
from langdetect import detect

In [2]:
pd.set_option('display.max_rows', 500)

In [3]:
df_tweets = pd.read_csv("datasets/tweet_dataset.csv")

In [4]:
df_tweets = df_tweets.rename(columns={"tweets": "uncleaned_text"})
df_tweets["emoji"] = ""
df_tweets["emoji_text"] = ""
df_tweets["text"] = ""
df_tweets["url"] = ""
df_tweets["tags"] = ""
df_tweets

id                                     uncleaned_text  \
0      787405734442958848  We can't extract the\n"Avenge" from\n"Scavenge...   
1      787405734442958848  We can't get the\n"Other" out of\n"Geothermal"...   
2      787405734442958848  You can't spell\n"Panoply"\nwithout "Ply" http...   
3      787405734442958848  Put the "Myrrh"\nin "Commercial" https://t.co/...   
4      787405734442958848  We need "Dying"\nto spell "Muddying" https://t...   
...                   ...                                                ...   
88127           524121160          혁아! 🐶\n#StayForMe https://t.co/kfFSga83RW   
88128           524121160                 만나서 알려줄거야🙃 https://t.co/VS3mHXkZYU   
88129           524121160  💐 https://t.co/hhfB4q2GkD https://t.co/wzlXNKxGCi   
88130           524121160  오늘 #정택운 하는 날☺️\n#레오 #LEO #Losing_Game\n#Piano_...   
88131           524121160  Choreography Mashup ll 🎁\n\n#achahakyeon #Chor...   

      account_type emoji emoji_text text url tags  
0              bot                                 
1              bot                                 
2              bot                                 
3              bot                                 
4              bot                                 
...            ...   ...        ...  ...  ..  ...  
88127        human                                 
88128        human                                 
88129        human                                 
88130        human                                 
88131        human                                 

[88132 rows x 8 columns]

In [5]:
def emoji_code_text(df):
    for word in range(len(df)):
        # Replace Unicode
        text = df["uncleaned_text"][word]
        #Accumalating all the emojis
        all_emojis = ''.join(x for x in text if emoji.is_emoji(x))
        emoji_dict = dict()
        emoji_word_list = []
        try:
            #For each emoji, decode it and add the decoding into the dictionary and the list
            for each_emoji in all_emojis:
                decoded = emoji.demojize(each_emoji)
                decoded = decoded.replace(':', '')
                emoji_dict[each_emoji] = decoded
                emoji_word_list.append(decoded)
            df["emoji"][word] = emoji_dict
            df["emoji_text"][word] = emoji_word_list
        except UnicodeDecodeError:
            df["emoji"][word] = dict()
            df["emoji_text"][word] = []
    return df

In [6]:
def url_text(df):
    #Extract URLs from tweets
    pattern = r'(https?:\/\/(?:www\.)?[-a-zA-Z0-9@:%._+~#=]{1,256}\.[a-zA-Z0-9()]{1,6}[-a-zA-Z0-9()@:%_+.~#?&/=]*)' 
    df['url']= df["uncleaned_text"].str.extract(pattern, expand=True)
    return df

In [7]:
#Extracting tagged accounts and storing them
def tags_in_text(df):
    for word in range(len(df)):
        tweet = df["uncleaned_text"][word]
        #Splitting the text into a list
        word_list = tweet.split(' ')
        tag_list = []
        #looping through the list 
        for idx in range(len(word_list)):
            each_word = word_list[idx]
            #If the word starts with @ it means it is a tagged account
            if each_word.startswith("@"):
                #Replace the invalid characters in the tagged name 
                each_word = re.sub("[^A-Za-z0-9-@-_]", "", each_word)
                word_list[idx] = ""
                #store the processed name in the list
                tag_list.append(each_word)
        #the list is stored in the tags column of the dataframe
        df["tags"][word] = tag_list
    return df

In [8]:
def tags_in_tweet(text):
    #This function removes all tagged accounts from the tweet because we have already stored it
    word_list = text.split(' ')
    tag_list = []
    for idx in range(len(word_list)):
        each_word = word_list[idx]
        if each_word.startswith("@"):
            each_word = re.sub("[^A-Za-z0-9-@-_]", "", each_word)
            word_list[idx] = ""
            tag_list.append(each_word)
    word_list = list(filter(lambda val: val != "", word_list))
    new_tweet = " ".join(word_list)
    return new_tweet

In [9]:
def decode_texts(text):
    #Decoding text from utf-8 encoding
    decoded = str(BeautifulSoup(text, from_encoding='utf8'))
    CLEANR = re.compile('<.*?>') 
    cleantext = re.sub(CLEANR, '', decoded)
    return cleantext

In [10]:
def review_to_words(text):
    # Remove URL
    pattern = r'(https?:\/\/(?:www\.)?[-a-zA-Z0-9@:%._+~#=]{1,256}\.[a-zA-Z0-9()]{1,6}[-a-zA-Z0-9()@:%_+.~#?&/=]*)' 
    text = re.sub(pattern, '', text)
    # Remove HTML
    review_text = BeautifulSoup(text).get_text()
    without_tags = tags_in_tweet(review_text)
    # Only keep letters and numbers
    letters_numbers_only = re.sub("[\W_]+", " ", without_tags) 
    words = letters_numbers_only.lower().split()  
    joint_tweet = " ".join(words)
    decoded_tweet = decode_texts(joint_tweet)
    return decoded_tweet

def words_text(df):
    num_tweets = df["uncleaned_text"].size
#     df["uncleaned_text"] = df["uncleaned_text"] + " " + df["emoji_text"]
    for word in range(num_tweets):
        df["text"][word] = review_to_words(df["uncleaned_text"][word])
    return df

In [11]:
#Applying the above defined functions to the dataset
df_tweets = emoji_code_text(df_tweets)
df_tweets = url_text(df_tweets)
df_tweets = tags_in_text(df_tweets)
df_tweets = words_text(df_tweets)
df_tweets

C:\Users\EMILYK~1\AppData\Local\Temp/ipykernel_25132/1734113815.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["emoji"][word] = emoji_dict
C:\Users\EMILYK~1\AppData\Local\Temp/ipykernel_25132/1734113815.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["emoji_text"][word] = emoji_word_list
C:\Users\EMILYK~1\AppData\Local\Temp/ipykernel_25132/872550287.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_tweets["tags"]

id                                     uncleaned_text  \
0      787405734442958848  We can't extract the\n"Avenge" from\n"Scavenge...   
1      787405734442958848  We can't get the\n"Other" out of\n"Geothermal"...   
2      787405734442958848  You can't spell\n"Panoply"\nwithout "Ply" http...   
3      787405734442958848  Put the "Myrrh"\nin "Commercial" https://t.co/...   
4      787405734442958848  We need "Dying"\nto spell "Muddying" https://t...   
...                   ...                                                ...   
88127           524121160          혁아! 🐶\n#StayForMe https://t.co/kfFSga83RW   
88128           524121160                 만나서 알려줄거야🙃 https://t.co/VS3mHXkZYU   
88129           524121160  💐 https://t.co/hhfB4q2GkD https://t.co/wzlXNKxGCi   
88130           524121160  오늘 #정택운 하는 날☺️\n#레오 #LEO #Losing_Game\n#Piano_...   
88131           524121160  Choreography Mashup ll 🎁\n\n#achahakyeon #Chor...   

      account_type                      emoji          emoji_text  \
0              bot                         {}                  []   
1              bot                         {}                  []   
2              bot                         {}                  []   
3              bot                         {}                  []   
4              bot                         {}                  []   
...            ...                        ...                 ...   
88127        human          {'🐶': 'dog_face'}          [dog_face]   
88128        human  {'🙃': 'upside-down_face'}  [upside-down_face]   
88129        human           {'💐': 'bouquet'}           [bouquet]   
88130        human      {'☺': 'smiling_face'}      [smiling_face]   
88131        human      {'🎁': 'wrapped_gift'}      [wrapped_gift]   

                                                    text  \
0            we can t extract the avenge from scavengers   
1               we can t get the other out of geothermal   
2                    you can t spell panoply without ply   
3                            put the myrrh in commercial   
4                        we need dying to spell muddying   
...                                                  ...   
88127                                       혁아 stayforme   
88128                                          만나서 알려줄거야   
88129                                                      
88130      오늘 정택운 하는 날 레오 leo losing game piano man op 9   
88131  choreography mashup ll achahakyeon choreograph...   

                           url tags  
0      https://t.co/FpAstfF67l   []  
1      https://t.co/pw6xYLUph5   []  
2      https://t.co/XYsPhTkcDX   []  
3      https://t.co/yyadIxV48k   []  
4      https://t.co/WJxZL1TkfM   []  
...                        ...  ...  
88127  https://t.co/kfFSga83RW   []  
88128  https://t.co/VS3mHXkZYU   []  
88129  https://t.co/hhfB4q2GkD   []  
88130  https://t.co/h5kv3eJ5Il   []  
88131  https://t.co/ZfG2oqGCGy   []  

[88132 rows x 8 columns]

In [15]:
def all_numbers(inputString):
    return all(char.isdigit() for char in inputString)

def drop_non_english(df):
    for word in range(len(df)):
        #Accessing the ith tweet
        tweet = df["text"][word]
        print(tweet)
        try:
            #If the tweet is acsii characters
            if (tweet.isascii()):
                #If the tweet is not empty and not all numbers and english is detected
                if (tweet != '') and not all_numbers(tweet) and (detect(tweet) == 'en'):
                    #no change to the df
                    df = df
                else:
                    #if not drop the particular row
                    df = df.drop(labels=[word], axis=0) 
            else:
                #if tweet non-ascii, drop that row
                df = df.drop(labels=[word], axis=0)
        except:
            #in the event of an exception in the above lines, drop that row
            df = df.drop(labels=[word], axis=0)
    #resetting the index after dropping the rows            
    df = df.reset_index(drop = True, inplace = False)
    return df

In [13]:
df_tweets

id                                     uncleaned_text  \
0      787405734442958848  We can't extract the\n"Avenge" from\n"Scavenge...   
1      787405734442958848  We can't get the\n"Other" out of\n"Geothermal"...   
2      787405734442958848  You can't spell\n"Panoply"\nwithout "Ply" http...   
3      787405734442958848  Put the "Myrrh"\nin "Commercial" https://t.co/...   
4      787405734442958848  We need "Dying"\nto spell "Muddying" https://t...   
...                   ...                                                ...   
88127           524121160          혁아! 🐶\n#StayForMe https://t.co/kfFSga83RW   
88128           524121160                 만나서 알려줄거야🙃 https://t.co/VS3mHXkZYU   
88129           524121160  💐 https://t.co/hhfB4q2GkD https://t.co/wzlXNKxGCi   
88130           524121160  오늘 #정택운 하는 날☺️\n#레오 #LEO #Losing_Game\n#Piano_...   
88131           524121160  Choreography Mashup ll 🎁\n\n#achahakyeon #Chor...   

      account_type                      emoji          emoji_text  \
0              bot                         {}                  []   
1              bot                         {}                  []   
2              bot                         {}                  []   
3              bot                         {}                  []   
4              bot                         {}                  []   
...            ...                        ...                 ...   
88127        human          {'🐶': 'dog_face'}          [dog_face]   
88128        human  {'🙃': 'upside-down_face'}  [upside-down_face]   
88129        human           {'💐': 'bouquet'}           [bouquet]   
88130        human      {'☺': 'smiling_face'}      [smiling_face]   
88131        human      {'🎁': 'wrapped_gift'}      [wrapped_gift]   

                                                    text  \
0            we can t extract the avenge from scavengers   
1               we can t get the other out of geothermal   
2                    you can t spell panoply without ply   
3                            put the myrrh in commercial   
4                        we need dying to spell muddying   
...                                                  ...   
88127                                       혁아 stayforme   
88128                                          만나서 알려줄거야   
88129                                                      
88130      오늘 정택운 하는 날 레오 leo losing game piano man op 9   
88131  choreography mashup ll achahakyeon choreograph...   

                           url tags  
0      https://t.co/FpAstfF67l   []  
1      https://t.co/pw6xYLUph5   []  
2      https://t.co/XYsPhTkcDX   []  
3      https://t.co/yyadIxV48k   []  
4      https://t.co/WJxZL1TkfM   []  
...                        ...  ...  
88127  https://t.co/kfFSga83RW   []  
88128  https://t.co/VS3mHXkZYU   []  
88129  https://t.co/hhfB4q2GkD   []  
88130  https://t.co/h5kv3eJ5Il   []  
88131  https://t.co/ZfG2oqGCGy   []  

[88132 rows x 8 columns]

In [16]:
df_tweets = drop_non_english(df_tweets)

we can t extract the avenge from scavengers
we can t get the other out of geothermal
you can t spell panoply without ply
put the myrrh in commercial
we need dying to spell muddying
trees on the shore at point lobos state natural reserve just outside carmel ca landscape photography
vintage photos of insects and spiders in vivid detail via
beware amazon still sells counterfeit memory cards
devils tower around sunset famous as the landing place in the movie close encounters of the third kind landscape photography
friday s stream starting at 10pm pt let s grind some events and eat gold giveaway stop by the stream and enter for a chance to win up to 100k gold on pc na or eu you must be a follower and in chat to win follow here
woot now go get your stuff
omg how are you holding up
did you get your bag of yet so cool to see eso on the front also the in game mount is stellar plus the free month of and i haven t even opened the bag
inevitable
one goal behind rivaldo and suarez in champions leag

your next flooring project doesn t have to be inside explore these terrace flooring ideas
our stunning floorcraft floors are just as stylish as they are durable
you ll stress less over a pet mess with our stain resistant stainmaster carpet underfoot
here are the most popular trends based on age where do you see your favorite design
millennial pink is popping up in home decor and on fashion runways everywhere
hein
erreur de jugement de ma part sur la température des pneus
ma petite domingo à 200km h vous imaginez bien que j ai revu mes objectifs à la baisse pour demain juste survivre c est déjà pas mal
frérot j ai spin à 200km h j ai plus confiance en moi j suis finito
thank you everyone for the well wishes had to have surgery again but it went great and i m recovering
we back
i m in let s do it
i m experimenting with just a quick 5 second shot i have the environment in ue and i recorded footage with a tracker on the camera using livelink only thing i m really having trouble with is lin

no calcularon todo el 2019 no los últimos 6 meses nadie de mi círculo lo recibio
calculan a 12 meses no era el promedio de los 6 últimos del 2019
bonoclasemedia2021 sii informa que será calculo sobre los 6 meses del segundo semestre entras al cálculo y te lo promedian a 12 meses jajaja
n c s two top democratic state officials are urging the republican led legislature to decriminalize the possession of small amounts of marijuana in light of biden s pardon of thousands of americans convicted of simple possession under federal law
beasley and budd debate in nc as national democrats spend elsewhere listen to the new episode of the politics podcast in your podcast feed now
democrat cheri beasley and republican ted budd the two major party candidates seeking to succeed retiring north carolina republican sen richard burr are meeting tonight for what is likely their only televised debate
show your love for wunc wherever you go with our new tote request yours today when you make a gift of 6 per

jerry jeudy
cena de luta davi vs golias
cineholliúdy2
leoncio ruim todo cineholliudy2
fazia tempo que não me divertia tanto num trabalho ciniholliúdy
is it too much to ask for a camera angle from the east side of the field hornsup usfbulls
the game to start weatherdelay
this is how you tailgate in florida floridasummer gobulls usfbulls hornsup
this is how you tailgate in florida floridasummer gobulls usfbulls hornsup
first thought when it comes to crusader hand grenades

after years of flying with i have decided to stop flying with this airline the rudest customer service i have ever met please resume services so we can all fly happily again
my only resolution for 2021 is to be healthy and happy
thank you for the updates and your expertise paul much appreciated
can we get some positive vibes for tampa st petersburg and clearwater area really all of florida it would be fun to get you to the straz center in tampa again
moistly harmless is the best zarking book title ever
new arrivals at 

the only way to keep up mortgage demand while rates spike
equity
yea this is good good news
leggi l editoriale completo in edicola e su fq extra
leggi l editoriale completo in edicola e su fq extra
leggi l editoriale completo in edicola e su fq extra
thank you
thank you
hope you feel better my friend
it s been a long week and just need some sleep i am settling in the new place well i hope everyone is doing well have a good good night everyone
nintendo is really hating on ya ll tech my switch worked for over a month just fine after using ya ll dock then i got an update and it stopped charging recommend offer ppl usb c cable with adaptive fast charger works till they get the tech ban lifted
pastor sharpe
yooooooooo
has it been reported on any media
we waiting on this
matt walsh every person in the dating scene right now would be happier if they were just matched up with someone against their will he is endorsing forced marriage here in the uk that is against the law
colonialism and repro

...

this is going to be incredible
abolish the filibuster pack the courts do anything and everything to protect rights for all people against far right minoritarian rule by a judiciary hostile to progress and equity
republicans have been working toward creating a court to strike down any legislation that doesn t align with their values for decades that time has arrived now it s roe v wade tomorrow it ll be anti discrimination laws or the right to marry it s time to fight
amarte
shuuuuu 6 años apoyándote mianiversariodetwitter
goooood morning sojo pitties dogsofinstagram ilovemydog adoptdontshop
lassie wants to play with her toys and invade your personal space at the same time adoptable
nakia is one happy pup adoptable bulldog bulldogmix dogsofinstagram adoptdontshop austin
so snug sojo pitties dogsofinstagram ilovemydog adoptdontshop
i asked for a cat but instead i adopted a pokemon ember flamepointsiamese catsofinstagram
questa storia delle bollette e una truffa colossale chi da energia s

mengão na final da copa do brasil e libertadores vamos flamengo
está na hora de garantir a vaga na final vamos mengão ad
perlu dicoba nih bisa dapet dimana
all our love from u k i m on 4th jab but still got it not nice but it peaks then goes keep that strength going we love you over here
you have it all use it wisely and save the planet peace and love
it looks like an english garden on a sunny day wonderful
happy days love from a freezing u k
omgoodness soooooooo beautiful looks like christmas eve magic for 1st week
me tooooo
happy birthday jonah

accept
thank you i hope that for you too
eatsa is back somehow
when we talk about tech providers disrupting the grocery industry simbe robotics comes first the robots developed by the startup automate the most monotonous redundant tasks in the grocery and retail industry simbe launched its first robot called tal
great announcement from decathlon ukraine we are happy to announce that decathlon is back to work this friday september 30 all our s

evoterra i ve listened to a lot of fiction podcasts over the years and it s led me to a singular realization audiodrama fictionpodcasts
evoterra oh
bible connection podcast designing the word with klaus krogh via
happy oceansday video the navigational miracle of sea turtles oceanday oceansday2022 oceanday2022 bible seaturtle seaturtles
i was there so freaking great
oh we re going on a solid run here
so much colder by the end than i planned for when i left home checks notes in the early afternoon
another year another great expoeast the brands and exhibitors did not disappoint and i saw many friends new and old as always i returned home with a bounty of snacks and treats i am am lucky to have such a fun job
this is about bill right
الصور اعلاه من مزرعة الهالكين الحوثيين خامنئي اصدر فتوى للحوثيين بزراعة جثث القتلى عشان تثمر لهم مقاتلين جدد
الاهلي شالسالفة كان الله بعون جماهيره وعون كل متابعي كرة القدم السعودية اعتقد التفريط باللاعبين الكبار أثر وبشكل كبير على مستوى الفريق يحزننا أن يكون و

اسقاط القروض مطلب شعبي انا كمواطن اطالب باسقاط القروض عاجلا غير اجل لان خلاص طفح الكيل ذبحتنا القروض مو قادرين انتنفس خيرنا المفروض لنا مو هبات لدول مادري شنو
10 ابتسامات
مغامرون يكتشفون شي غريب بين الجبال
trump is as intimidated by beto as he is obama beto2020
and this body
come on dwts31
did she pay her pimp rhoa latoya
apakah vokalis kami kurang terkenal
jarang ini
band2 yang lagi minsiv dengerin akhir2 ini hursa perunggu sama the dare kalo kamu band apa
gak sekalian pok ame2
tungguin ya

yo la banco y los banco fuerte me la bajan los criticadores seriales
una locuraaaaa
اگر زن بخواهد در کنار زنان ایرانی هستم که باشجاعت نشان دادن اگر زن بخواهد می تواند هر گونه صدای را خاموش کند باید ساکت شوید نمی توانید با زورگوی و سرکوب کردن به پوشش زنان دخالت کنید نمی توانید هیچ زنی را بابت پوششش محاکمه کنید ویا بکشید هیچ زنی بابت پوشش مسحق کشته شدن نیست
kadın isterse bir gün herkesin susmak zorunda olduğunu gösteren i̇ranlı kadınlara hayranım yanlarındayım susacaksiniz hiçbir kadın giyiminden dol

just posted a photo
let s place some pcl screw threads in my neck these polycaprolactone last the longest in the skin building collagen and elastin for 2 years i got them at acecosm and code jessica10 saves you money watch now diypclthreads diypcltreatment
it s election season y all join secretary of state at the 2022 california fall youth vote summit hear from state leaders how to make an impact in your community and more castudentsvoteproject

a lot of superpowers in that room
thanks nadine
love it

3 the above are reposts due to prior typos grammar errors yes this is the second repost time to get off twitter we don t have a complete picture of what happened but it s clear that over time as noted in 2 things got toxic this is not to question either side s veracity
2 the change on primary day the woman texted walker s wife he ll do great you will keep him focused proud of you guys wishing nothing but the best for you tonight today she texted did you know herschel paid for my abortion 

In [17]:
df_tweets

id                                     uncleaned_text  \
0      787405734442958848  We can't extract the\n"Avenge" from\n"Scavenge...   
1      787405734442958848  We can't get the\n"Other" out of\n"Geothermal"...   
2      787405734442958848  You can't spell\n"Panoply"\nwithout "Ply" http...   
3      787405734442958848  Put the "Myrrh"\nin "Commercial" https://t.co/...   
4      787405734442958848  We need "Dying"\nto spell "Muddying" https://t...   
...                   ...                                                ...   
53679           587035713  Lung Cancer: Help Make the Invisible Disease V...   
53680           587035713  Can Mushrooms Help the Immune System Fight Can...   
53681          3259069508  @davidhelman_ @CowboysNation For real! Holy **...   
53682          3259069508      @UberFacts They paid $2.5 million. #uberfacts   
53683           524121160  Choreography Mashup ll 🎁\n\n#achahakyeon #Chor...   

      account_type                  emoji      emoji_text  \
0              bot                     {}              []   
1              bot                     {}              []   
2              bot                     {}              []   
3              bot                     {}              []   
4              bot                     {}              []   
...            ...                    ...             ...   
53679          bot                     {}              []   
53680          bot                     {}              []   
53681        human                     {}              []   
53682        human                     {}              []   
53683        human  {'🎁': 'wrapped_gift'}  [wrapped_gift]   

                                                    text  \
0            we can t extract the avenge from scavengers   
1               we can t get the other out of geothermal   
2                    you can t spell panoply without ply   
3                            put the myrrh in commercial   
4                        we need dying to spell muddying   
...                                                  ...   
53679  lung cancer help make the invisible disease vi...   
53680  can mushrooms help the immune system fight can...   
53681  for real holy i don t understand how so many p...   
53682                    they paid 2 5 million uberfacts   
53683  choreography mashup ll achahakyeon choreograph...   

                           url                             tags  
0      https://t.co/FpAstfF67l                               []  
1      https://t.co/pw6xYLUph5                               []  
2      https://t.co/XYsPhTkcDX                               []  
3      https://t.co/yyadIxV48k                               []  
4      https://t.co/WJxZL1TkfM                               []  
...                        ...                              ...  
53679  https://t.co/IB1idH6a9B                               []  
53680  https://t.co/9uQR8dN1cA                               []  
53681                      NaN  [@davidhelman_, @CowboysNation]  
53682                      NaN                     [@UberFacts]  
53683  https://t.co/ZfG2oqGCGy                               []  

[53684 rows x 8 columns]

In [19]:
df_tweets.to_csv('datasets\cleaned_tweets_dataset.csv', index = False)